In [9]:
import requests
import json
import os
import sys
import pandas as pd
import logging
from urllib.parse import urlencode
import time
from datetime import timedelta, datetime

In [ ]:
def get_unix_time(days_ago=0):   
    """
    Convert days_ago to a unix timestamp
    
    Parameters:
    days_ago (int): Number of days in the past
    
    Returns:
    int: Unix timestamp for the date that was 'days_ago' days ago
    """
    current_time = int(time.time())
    seconds_ago = int(timedelta(days=days_ago).total_seconds())
    return current_time - seconds_ago

def get_time_delta(min_unix_time,max_time):
    """Returns string for url if short=False, else just the int"""
    min_unix_time = int(time.time()) #current time
    return (int(min_unix_time - timedelta(days=max_time).total_seconds()))

In [23]:
def fetch_match_data(
    min_average_badge: int = 100,
    max_unix_timestamp: int | None = None,
    min_unix_timestamp: int | None = None,
    m_id: str | None = None,
    include_player_info: bool = True,
    limit: int = 1000
    ) -> json:
    """Fetches match data from the Deadlock API.
    
    Key Parameters:
    - min_average_badge: Minimum average rank to return matches.
    - max_unix_timestamp: Newest time to filter matches. i.e. matches before yesterday
    - min_unix_timestamp: Oldest time to filter matches. i.e. matches 3 months ago -> max time
    - m_id: Specific match ID to fetch metadata for.
    - include_player_info: Whether to include player information in the response. this is required for match_player data
    - limit: Maximum number of matches to return.
    Returns:
    - JSON response containing match metadata with 12 players per match.
    """

    logging.debug(f"Fetching match data..")
    base = "https://api.deadlock-api.com/v1/matches"

    # if a specific match ID is given, check player_data and hit that endpoint
    if m_id:
        path = f"{base}/{m_id}/metadata"
        params = {}
        if include_player_info:
            params["include_player_info"] = "true"

        query = urlencode(params)
        full_url = f"{path}?{query}" if query else path
        response = requests.get(full_url)
        if response.status_code != 200:
            print(f"Error: API request failed with status code {response.status_code}")
            print(f"URL: {full_url}")
            return {"error": f"API request failed with status code {response.status_code}"}
        return response.json()

    # Bulk-metadata endpoint
    path = f"{base}/metadata"
    params: dict[str, str] = {}

    if include_player_info:
        params["include_player_info"] = "true"
    
    # Convert days to unix timestamps - ensure max is newer (smaller days_ago) than min
    if min_unix_timestamp is not None:
        older_time = get_unix_time(min_unix_timestamp)
        params["min_unix_timestamp"] = str(older_time)
    if max_unix_timestamp is not None:
        newer_time = get_unix_time(max_unix_timestamp)
        params["max_unix_timestamp"] = str(newer_time)
        
        # Debug info for timestamps
        print(f"Time range: {max_unix_timestamp} days ago to {min_unix_timestamp} days ago")
        print(f"Unix timestamps: {newer_time} to {older_time}")
        
    if min_average_badge is not None:
        params["min_average_badge"] = str(min_average_badge)
    if limit is not None:
        params["limit"] = str(limit)

    query = urlencode(params)
    full_url = f"{path}?{query}" if query else path
    
    print(f"Making request to: {full_url}")
    response = requests.get(full_url)
    if response.status_code != 200:
        print(f"Error: API request failed with status code {response.status_code}")
        print(f"URL: {full_url}")
        return {"error": f"API request failed with status code {response.status_code}"}
    return response.json()

In [6]:
data = fetch_match_data(limit=10)
data

[{'average_badge_team0': 102,
  'average_badge_team1': 102,
  'duration_s': 1267,
  'game_mode': 'Normal',
  'game_mode_version': None,
  'is_high_skill_range_parties': False,
  'low_pri_pool': False,
  'match_id': 28627568,
  'match_mode': 'Unranked',
  'match_outcome': 'TeamWin',
  'new_player_pool': False,
  'players': [{'abandon_match_time_s': 0,
    'ability_points': 20,
    'account_id': 100051626,
    'assigned_lane': 3,
    'assists': 9,
    'deaths': 3,
    'denies': 10,
    'hero_id': 19,
    'kills': 10,
    'last_hits': 94,
    'net_worth': 21578,
    'party': 1,
    'player_level': 25,
    'player_slot': 9,
    'team': 'Team1'},
   {'abandon_match_time_s': 0,
    'ability_points': 22,
    'account_id': 91308342,
    'assigned_lane': 4,
    'assists': 10,
    'deaths': 5,
    'denies': 13,
    'hero_id': 12,
    'kills': 8,
    'last_hits': 150,
    'net_worth': 27204,
    'party': 0,
    'player_level': 27,
    'player_slot': 11,
    'team': 'Team1'},
   {'abandon_match_ti

In [24]:
def bulk_fetch_matches(max_days_fetch=90, min_days=3, max_days=0)->json:
    """fetches a batch of matches, 1 day per pull, returns json and exports.

    batch is unnormalized, 'players' contains a df of each matches 'players'
    
    limit = max matches within a day to pull
    min_days = Oldest time barrier (more days ago)
    max_days = Newest time barrier (fewer days ago)
    max_days_fetch = max days to fetch, starting from max_days
    
    example:
    bulk_fetch_matches(max_days_fetch=30, min_days=7, max_days=0)
    will fetch data in one-day increments, from today back to 7 days ago,
    or until 30 days of data have been fetched.
    """

    limit = 500
    batch_matches = []
    
    # Calculate the starting day (defaults to today)
    current_max = max_days      # Newer boundary (fewer days ago)
    current_min = current_max + 1  # Older boundary (more days ago)
    
    for batch in range(max_days_fetch):
        logging.debug(f"\nBatch {batch}: fetching day from {current_max} to {current_min} days ago")
        print(f"DEBUG: Fetching matches for day {batch + 1} from {current_max} to {current_min} days ago")
        
        # Note: API expects min_unix_timestamp to be OLDER than max_unix_timestamp
        fetched_matches = fetch_match_data(
            min_unix_timestamp=current_min,  # Older timestamp (more days ago)
            max_unix_timestamp=current_max,  # Newer timestamp (fewer days ago)
            limit=limit
        )
        
        # Check if there was an error in the API response
        if "error" in fetched_matches:
            print(f"Error encountered during batch {batch+1}. Skipping this batch.")
        else:
            batch_matches.append(fetched_matches)
            
        # Move backward in time by one day
        current_max += 1  # Increase days ago for newer boundary
        current_min += 1  # Increase days ago for older boundary
        
        # Stop if we've reached the minimum days boundary
        if current_max >= min_days:
            print(f"Reached configured minimum day boundary ({min_days} days ago)")
            break

    return batch_matches

In [25]:
print("Testing fixed bulk fetch - getting data from today to 3 days ago")
data = bulk_fetch_matches(max_days_fetch=4, min_days=3, max_days=0)
# Show how many matches we got in each day
for i, day_data in enumerate(data):
    if "error" in day_data:
        print(f"Day {i}: Error")
    else:
        print(f"Day {i}: {len(day_data)} matches")
data

Testing fixed bulk fetch - getting data from today to 3 days ago
DEBUG: Fetching matches for day 1 from 0 to 1 days ago
Time range: 0 days ago to 1 days ago
Unix timestamps: 1754661993 to 1754575593
Making request to: https://api.deadlock-api.com/v1/matches/metadata?include_player_info=true&min_unix_timestamp=1754575593&max_unix_timestamp=1754661993&min_average_badge=100&limit=500
DEBUG: Fetching matches for day 2 from 1 to 2 days ago
Time range: 1 days ago to 2 days ago
Unix timestamps: 1754575593 to 1754489193
Making request to: https://api.deadlock-api.com/v1/matches/metadata?include_player_info=true&min_unix_timestamp=1754489193&max_unix_timestamp=1754575593&min_average_badge=100&limit=500
DEBUG: Fetching matches for day 2 from 1 to 2 days ago
Time range: 1 days ago to 2 days ago
Unix timestamps: 1754575593 to 1754489193
Making request to: https://api.deadlock-api.com/v1/matches/metadata?include_player_info=true&min_unix_timestamp=1754489193&max_unix_timestamp=1754575593&min_averag

[[{'average_badge_team0': 105,
   'average_badge_team1': 105,
   'duration_s': 2227,
   'game_mode': 'Normal',
   'game_mode_version': 2,
   'is_high_skill_range_parties': False,
   'low_pri_pool': False,
   'match_id': 38601458,
   'match_mode': 'Unranked',
   'match_outcome': 'TeamWin',
   'new_player_pool': False,
   'players': [{'abandon_match_time_s': 0,
     'ability_points': 27,
     'account_id': 373608909,
     'assigned_lane': 6,
     'assists': 20,
     'deaths': 5,
     'denies': 10,
     'hero_id': 31,
     'kills': 9,
     'last_hits': 107,
     'net_worth': 41944,
     'party': 0,
     'player_level': 31,
     'player_slot': 7,
     'team': 'Team1'},
    {'abandon_match_time_s': 0,
     'ability_points': 29,
     'account_id': 1070055248,
     'assigned_lane': 1,
     'assists': 12,
     'deaths': 6,
     'denies': 12,
     'hero_id': 3,
     'kills': 9,
     'last_hits': 165,
     'net_worth': 48978,
     'party': 0,
     'player_level': 33,
     'player_slot': 3,
     